In [1]:
import pandas as pd 
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm

# import cufflinks as cf
# from plotly import __version__
# from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

# cf.go_offline()

# %matplotlib inline
from sklearn.metrics import mean_absolute_error, mean_absolute_percentage_error, mean_squared_error

from neuralforecast.auto import AutoLSTM
from neuralforecast.tsdataset import TimeSeriesDataset
from neuralforecast.core import NeuralForecast
from neuralforecast.models import LSTM

from datetime import datetime, timedelta
# import plotly.graph_objects as go
# import matplotlib.colors as mcolors
from neuralforecast.losses.pytorch import MQLoss
from tqdm import tqdm

In [2]:
# Load and process the MEASLES_ARIZONA data
df = pd.read_csv("../outbreaks_disease_location.csv")
value_columns = [str(i) for i in range(60)]
series_values = df[value_columns].fillna(0).astype(float)
start_dates = pd.to_datetime(df["start_date"])

# Shuffle and split
shuffled_indices = df.sample(frac=1, random_state=42).index
split_point = int(0.8 * len(df))
train_indices = shuffled_indices[:split_point]
test_indices = shuffled_indices[split_point:]

In [3]:
train_records = []
for i, row in series_values.iloc[train_indices].iterrows():
    dates = pd.date_range(start="2000-01-01", periods=60, freq="W-SAT")
    for t, value in enumerate(row):
        train_records.append({"unique_id": f"Y{i+1}", "ds": dates[t], "y": value})
df_train = pd.DataFrame(train_records)

test_start_dates = start_dates.loc[test_indices] - pd.Timedelta(weeks=4)
df_test_all = []

for idx in test_indices:
    start_date = test_start_dates.loc[idx]
    row = series_values.loc[idx]
    dates = pd.date_range(start=start_date, periods=60, freq="W-SAT")
    for t, value in enumerate(row):
        df_test_all.append({"unique_id": f"Y_{idx}", "ds": dates[t], "y": value})

df_test_all = pd.DataFrame(df_test_all)

In [4]:
df_train["date"] = pd.to_datetime(df_train["ds"])
df_train.set_index("date", inplace = True)

df_test_all["date"] = pd.to_datetime(df_test_all["ds"])
df_test_all.set_index("date", inplace = True)

In [5]:
df_test_all.head()

unique_id         ds        y
date                                    
2022-08-13    Y_5607 2022-08-13  20775.0
2022-08-20    Y_5607 2022-08-20  16570.0
2022-08-27    Y_5607 2022-08-27  13995.0
2022-09-03    Y_5607 2022-09-03  12145.0
2022-09-10    Y_5607 2022-09-10  10686.0

In [6]:
class FixedModelLSTMProcessor:
    def __init__(self, dates=[]):
        self.dates = dates            # updated dynamically during evaluation
        self.forecasts = []
        self.eval_pairs = []          # (forecast_df, ground_truth_df)
        self.input_size = None
        self.nf = None
        self.config = None
        self.testset = None
        self.maes = []
        self.mses = []
        self.mapes = []
        self.nmses = []
        self.reference_dates = {}
        self.metrics_df = pd.DataFrame(columns=["Unique_id","Reference Date", "MAE", "MSE", "MAPE", "NMSE"])
        self.display_df = pd.DataFrame(columns=["Unique_id","Reference Date", "Target End Date", "GT" , "Quantile", "Prediction"])
        self.color_mapping = {}
        self.model = None
        self.selected_input_size = None
        self.uid_forecast = []
        self.uid_eval_pairs = []

    def create_fixed_model(self, df_train, df_test, test_ids, h, freq, model_name, level=[]):
        input_length = df_train.groupby("unique_id").size().min()
        max_input_size = max(8, input_length - h - 1)
        
        self.testset = df_test

        def config(trial):
            return {
                "input_size": trial.suggest_int("input_size", 8, max_input_size),
                "encoder_hidden_size": trial.suggest_categorical("encoder_hidden_size", [32, 64, 128]),
                "encoder_n_layers": trial.suggest_int("encoder_n_layers", 1, 3),
                "context_size": trial.suggest_int("context_size", 1, h),
                "decoder_hidden_size": trial.suggest_categorical("decoder_hidden_size", [32, 64, 128]),
                "learning_rate": trial.suggest_float("learning_rate", 1e-4, 1e-2, log=True),
                "batch_size": trial.suggest_categorical("batch_size", [16, 32, 64]),
                "random_seed": trial.suggest_int("random_seed", 1, 99999),
                "start_padding_enabled": True,
                "accelerator": "gpu",
                "devices": 2,
                "strategy": "auto"
            }

        self.config = config

        if not level:
            nf = NeuralForecast(models = [AutoLSTM(h = h, backend = "optuna",config=self.config)], freq = freq)
            nf.fit(df=df_train)
        else:
            nf = NeuralForecast(models = [AutoLSTM(h = h, backend = "optuna", loss = MQLoss(level = level),config=self.config)], freq = freq)
            nf.fit(df=df_train)
        
        self.nf = nf
        nf.save(path='./saved_models/LSTM/',
                model_index=None,
                overwrite=True,
                save_dataset=True)
        self.model = nf.models[0].model
        
        selected_input_size = nf.models[0].model.hparams['input_size']
        self.selected_input_size = selected_input_size

        for uid in test_ids:
            series_df = df_test[df_test["unique_id"] == uid]
            
            
            if len(series_df) <= selected_input_size:
                print(f"Skipping {uid}: length {len(series_df)} < required {selected_input_size}")
                continue
            
            reference_date = series_df["ds"].iloc[-4]
        
            self.reference_dates[uid] = reference_date

            forecast_date = pd.to_datetime(reference_date)
            df = series_df[series_df["ds"] <= forecast_date]
            forecast = nf.predict(df=df)
            forecast.set_index("ds", inplace=True)
        
            forecast_horizon = forecast.index
            ground_truth = series_df[series_df["ds"].isin(forecast_horizon)].set_index("ds")

            self.add_forecast_result(forecast_df=forecast, truth_df=ground_truth, reference_date=reference_date.strftime("%Y-%m-%d"))
    
    def efficient_compute_wis(self, display_df):
        display_df = display_df.sort_values(by=["Unique_id", "Reference Date", "Target End Date", "Quantile"])
        results = []
        grouped = display_df.groupby(["Unique_id", "Reference Date", "Target End Date"])

        for (uid, ref_date, tgt_date), group in tqdm(grouped, desc="Computing WIS"):
            gt = group["GT"].iloc[0]
            group = group.sort_values("Quantile")

            if not np.any(np.isclose(group["Quantile"], 0.5)):
                continue

            median_pred = group[np.isclose(group["Quantile"], 0.5)]["Prediction"].iloc[0]
            ae = abs(median_pred - gt)

            lo = group[group["Quantile"] < 0.5]
            hi = group[group["Quantile"] > 0.5][::-1].reset_index(drop=True)

            wis_components = []
            for i in range(min(len(lo), len(hi))):
                alpha = hi.iloc[i]["Quantile"] - lo.iloc[i]["Quantile"]
                lo_pred, hi_pred = lo.iloc[i]["Prediction"], hi.iloc[i]["Prediction"]
                interval_score = (
                    hi_pred - lo_pred
                    + (2 / alpha) * (lo_pred - gt) * (gt < lo_pred)
                    + (2 / alpha) * (gt - hi_pred) * (gt > hi_pred)
                )
                wis_components.append(interval_score)

            wis = (ae + np.sum(wis_components)) / (1 + len(wis_components))
            results.append({
                "Unique_id": uid,
                "Reference Date": ref_date,
                "Target End Date": tgt_date,
                "GT": gt,
                "WIS": wis
            })

        return pd.DataFrame(results)


    def forecasts_uid_date(unique_id,datetime):
        series_df = self.testset[self.testset["unique_id"] == uid]
        dt_index = np.where(series_df['ds'] == datetime)[0]
        if (df_index+1) <= self.selected_input_size:
            print(f"Skipping {uid}: length {df_index+1} < required {self.selected_input_size}")
            return 'Not valid input, too short'
        
        reference_date = datetime
        forecast_date = pd.to_datetime(reference_date)
        df = series_df[series_df["ds"] < forecast_date]
        uid_forecast = nf.predict(df=df)
        uid_forecast.set_index("ds", inplace=True)
        forecast_horizon = uid_forecast.index
        ground_truth = series_df[series_df["ds"].isin(forecast_horizon)].set_index("ds")
        
        return self.add_uid_forecast_result(forecast_df=uid_forecast, truth_df=ground_truth, reference_date=reference_date.strftime("%Y-%m-%d"))
    
    def add_uid_forecast_result(self, forecast_df, truth_df, reference_date):
        self.uid_forecast.append(forecast_df)
        self.uid_eval_pairs.append((forecast_df, truth_df))
        self.dates.append(reference_date)
    
    def add_forecast_result(self, forecast_df, truth_df, reference_date):
        self.forecasts.append(forecast_df)
        self.eval_pairs.append((forecast_df, truth_df))
        self.dates.append(reference_date)

    def calculate_metrics(self):
        for forecast_df, truth_df in self.eval_pairs:
            mae = mean_absolute_error(truth_df.iloc[:, 1], forecast_df.iloc[:, 1])
            mse = mean_squared_error(truth_df.iloc[:, 1], forecast_df.iloc[:, 1])
            mape = mean_absolute_percentage_error(truth_df.iloc[:, 1], forecast_df.iloc[:, 1])
            nmse = mse / np.var(truth_df.iloc[:, 1])

            self.maes.append(mae)
            self.mses.append(mse)
            self.mapes.append(mape)
            self.nmses.append(nmse)

    def display_maes(self):
        for i in range(len(self.maes)):
            date_obj = datetime.strptime(self.dates[i], "%Y-%m-%d")
            english_date = date_obj.strftime("%B %d, %Y")
            print(f"Mean Absolute Error for {english_date} model: {self.maes[i]}")

    def display_mses(self):
        for i in range(len(self.mses)):
            date_obj = datetime.strptime(self.dates[i], "%Y-%m-%d")
            english_date = date_obj.strftime("%B %d, %Y")
            print(f"Mean Squared Error for {english_date} model: {self.mses[i]}")

    def display_mapes(self):
        for i in range(len(self.mapes)):
            date_obj = datetime.strptime(self.dates[i], "%Y-%m-%d")
            english_date = date_obj.strftime("%B %d, %Y")
            print(f"Mean Absolute Percentage Error for {english_date} model: {self.mapes[i]}")

    def display_nmses(self):
        for i in range(len(self.nmses)):
            date_obj = datetime.strptime(self.dates[i], "%Y-%m-%d")
            english_date = date_obj.strftime("%B %d, %Y")
            print(f"Normalized Mean Square Error for {english_date} model: {self.nmses[i]}")

    def create_metrics_df(self):
        for i in range(len(self.dates)):
            self.metrics_df.loc[len(self.metrics_df)] = [
                self.dates[i], self.maes[i], self.mses[i], self.mapes[i], self.nmses[i]
            ]

    def efficient_create_display_df(self, forecasts, reference_dates, testset):
        records = []
        testset_indexed = testset.set_index(["unique_id", "ds"])

        for forecast_df in tqdm(forecasts, desc="Building display_df"):
            uid = forecast_df["unique_id"].iloc[0]
            reference_date = reference_dates[uid]
            gt_series = testset_indexed.loc[uid]["y"] if uid in testset_indexed.index.get_level_values(0) else pd.Series()

            for col in forecast_df.columns:
                if col == "unique_id":
                    continue

                if "lo" in col:
                    number = int(col[-2:])
                    alpha = 1 - (number / 100)
                    quantile = alpha / 2
                elif "hi" in col:
                    number = int(col[-2:])
                    alpha = 1 - (number / 100)
                    quantile = 1 - (alpha / 2)
                elif col in ["AutoLSTM-median", "AutoLSTM"]:
                    quantile = 0.5
                else:
                    continue

                df_col = forecast_df[[col]].copy()
                df_col.rename(columns={col: "Prediction"}, inplace=True)
                df_col["Unique_id"] = uid
                df_col["Reference Date"] = reference_date
                df_col["Target End Date"] = df_col.index
                df_col["GT"] = df_col.index.map(gt_series.get)
                df_col["Quantile"] = quantile
                records.append(df_col)

        df_out = pd.concat(records)
        return df_out[["Unique_id", "Reference Date", "Target End Date", "GT", "Quantile", "Prediction"]].sort_values(
            by=["Unique_id", "Reference Date", "Target End Date", "Quantile"]
        ).reset_index(drop=True)


    
    def generate_color_map(self, columns, cmap_name = "viridis"):
        intervals = set()
        for col in columns:
            if 'median' in col:
                continue
            parts = col.split('-')
            number = parts[-1]
            intervals.add(number)
        
        intervals = sorted(intervals, key=int)
        cmap = plt.cm.get_cmap(cmap_name)
        
        n = len(intervals)
        if n > 0:
            half = np.linspace(0.2, 0.45, n // 2, endpoint=True)[::-1]  # lower intervals
            upper = np.linspace(0.55, 0.8, n - n // 2, endpoint=True)  # higher intervals
            sample_points = np.concatenate([half, upper])
        else:
            sample_points = np.array([])  # just median
        
        median_value = np.median(sample_points)
        
        color_mapping = {}
        color_mapping['median'] = mcolors.to_hex(cmap(median_value))  # center of the colormap
        for interval, point in zip(intervals, sample_points):
            color_mapping[interval] = mcolors.to_hex(cmap(point))
    
        return color_mapping
    
    def create_graph(self):
        
        #Create color map for various confidence bands, only if levels are present
        if len(self.forecasts[0].columns) != 1:
            self.color_mapping = self.generate_color_map(columns = self.forecasts[0].columns)
                
        
        for i in range(len(self.forecasts)):
            #Plot the overall Real Data
            fig = go.Figure()
            fig.add_trace(go.Scatter(x = self.overall_df.index, y = self.overall_df[self.overall_df_value_col], mode = "lines", name = "Real Data"))

            
            for col in self.forecasts[i].columns:
                #Plot his first
                if "hi" in col:
                    number = col[-2:]
                    fig.add_trace(go.Scatter(x = self.forecasts[i].index, y = self.forecasts[i][col], mode = "lines", name = col, 
                                             line = dict(color = self.color_mapping[number])))
            
            for col in self.forecasts[i].columns:
                #Lows will go to corresponding his
                if "lo" in col:
                    number = col[-2:]
                    fig.add_trace(go.Scatter(x = self.forecasts[i].index, y = self.forecasts[i][col], mode = "lines", name = col, 
                                             fill = "tonexty", fillcolor = self.color_mapping[number], line = dict(color = self.color_mapping[number])))
            
            for col in self.forecasts[i].columns:
                #Median gets plotted last
                if "median" in col:
                    fig.add_trace(go.Scatter(x = self.forecasts[i].index, y = self.forecasts[i][col], mode = "lines", name = col, 
                                             line = dict(color = self.color_mapping["median"])))
            
            #Case for if confidence interval not present
            for col in self.forecasts[i].columns:
                if col == "AutoLSTM":
                    fig.add_trace(go.Scatter(x = self.forecasts[i].index, y = self.forecasts[i]["AutoLSTM"], mode = "lines", name = "AutoLSTM"))
            
            
            fig.update_layout(title = f"Fixed Parameter LSTM Predictions, {self.dates[i]}", xaxis_title = "Date", yaxis_title = "Count", hovermode = "x")
            fig.show()

In [7]:
test_ids = [f"Y_{i}" for i in test_indices]

In [8]:
processor = FixedModelLSTMProcessor()

In [9]:
processor.create_fixed_model(df_train, df_test_all, test_ids, h=4, freq="W-SAT", model_name="out_break_disease_LSTM", level = [10,20,30,40,50,60,70,80, 85,90,95])

[I 2026-02-06 18:53:07,393] A new study created in memory with name: no-name-1142390b-ad40-46c8-80cf-82e61c4828e5
[rank: 0] Seed set to 66892
/home/aa5dw/.local/lib/python3.12/site-packages/neuralforecast/models/lstm.py:167: UserWarning: context_size is deprecated and will be removed in future versions.
  warnings.warn(
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
💡 Tip: For seamless cloud logging and experiment tracking, try installing [litlogger](https://pypi.org/project/litlogger/) to enable LitLogger, which logs metrics and artifacts automatically to the Lightning Experiments platform.
Initializing distributed: GLOBAL_RANK: 0, MEMBER: 1/2
Initializing distributed: GLOBAL_RANK: 1, MEMBER: 2/2
----------------------------------------------------------------------------------------------------
distributed_backend=nccl
All distributed processes registered. Starting with 2 processes
----------------------------------------------------------------------

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.
/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.


Training: |          | 0/? [00:00<?, ?it/s]

/home/aa5dw/.local/lib/python3.12/site-packages/torch/autograd/graph.py:865: UserWarning: The AccumulateGrad node's stream does not match the stream of the node that produced the incoming gradient. This may incur unnecessary synchronization and break CUDA graph capture if the AccumulateGrad node's stream is the default stream. This mismatch is caused by an AccumulateGrad node created prior to the current iteration being kept alive. This can happen if the autograd graph is still being kept alive by tensors such as the loss, or if you are using DDP, which will stash a reference to the node. To resolve the mismatch, delete all references to the autograd graph or ensure that DDP initialization is performed under the same stream as subsequent forwards. If the mismatch is intentional, you can use torch.autograd.graph.set_warn_on_accumulate_grad_stream_mismatch(False) to suppress this warning. (Triggered internally at /pytorch/torch/csrc/autograd/input_buffer.cpp:240.)
  return Variable._exec

...

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
💡 Tip: For seamless cloud logging and experiment tracking, try installing [litlogger](https://pypi.org/project/litlogger/) to enable LitLogger, which logs metrics and artifacts automatically to the Lightning Experiments platform.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]
/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
💡 Tip: For seamless cloud logging and experiment tracking, try installing [litlogger](https://pypi.org/project/litlogger/) to enable LitLogger, which logs metrics and artifacts automatically to the Lightning Experiments platform.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]
/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.


Predicting: |          | 0/? [00:00<?, ?it/s]

In [10]:
display_df = processor.efficient_create_display_df(processor.forecasts, processor.reference_dates, processor.testset)

Building display_df: 100%|██████████| 2160/2160 [01:19<00:00, 27.11it/s]


In [11]:
display_df

Unique_id Reference Date Target End Date   GT  Quantile  Prediction
0            Y_1     2011-10-15      2011-10-15  0.0     0.025   -0.164432
1            Y_1     2011-10-15      2011-10-15  0.0     0.050   -0.006146
2            Y_1     2011-10-15      2011-10-15  0.0     0.075    0.000623
3            Y_1     2011-10-15      2011-10-15  0.0     0.100    0.002588
4            Y_1     2011-10-15      2011-10-15  0.0     0.150    0.005601
...          ...            ...             ...  ...       ...         ...
198715    Y_9999     1957-03-02      1957-03-23  0.0     0.850    1.251802
198716    Y_9999     1957-03-02      1957-03-23  0.0     0.900    1.374665
198717    Y_9999     1957-03-02      1957-03-23  0.0     0.925    1.520665
198718    Y_9999     1957-03-02      1957-03-23  0.0     0.950    1.659841
198719    Y_9999     1957-03-02      1957-03-23  0.0     0.975    1.928036

[198720 rows x 6 columns]

In [21]:
test_temp=df_test_all[df_test_all.unique_id=='Y_1']


In [24]:
processor.model.predict(test_temp.iloc[0])

AttributeError: 'Series' object has no attribute 'temporal_cols'

In [ ]:
temp[temp.Unique_id=='Y_1']['Reference Date'].unique()

In [12]:
display_df.to_csv('../../output/forecasts_LSTM.csv',index=None)

In [13]:
wis_table = processor.efficient_compute_wis(display_df)

Computing WIS: 100%|██████████| 8640/8640 [00:27<00:00, 317.09it/s]


In [14]:
np.mean(wis_table['WIS'].values)

np.float64(126.41802187804335)

In [15]:
wis_dfs = [wis_table.iloc[i::4].reset_index(drop=True) for i in range(4)]

In [16]:
np.mean(wis_dfs[3]['WIS'].values)

np.float64(49.93130306976028)

In [17]:
wis_table.to_csv('../../eval/WIS_LSTM.csv')